# Homework Assignment: Wonderlandia Election Simulation
## Basics of Programming in Python (Fall'22)

### Description 


In October 2022, elections were finished in Wonderlandia. At stake were 400 seats in the local parliament, and each seat is allocated through a **parallel voting**. Half of the seats are elected by party-list proportional representation (PLPR) with a minimum of 10% electoral threshold of number of votes that enable the party to get seats. The other half elected in single-member constituencies by first-past-the-post voting (plurality voting).

In this assigment, we offer you to code down an election process similar to Wonderlandia's one, with different voting systems (algorithms to compute an election's winner), including:
* Single-Member Plurality Voting (first-past-the-post)
* Borda count
* Condorcet method

### Goals

During the Homework Assignment, you will:
* prepare structurised report in Jupyter Notebook format that contain both detailed problem solving logic and its implementation with code;
* practice in basics of Python (variables, sequences, control flows, etc.);
* practice in stating conditions and and logical expressions from tasks of your assignment;
* apply acquired programming skills for solving practical political science problem.

### Organizational stuff

Separate links to submit [Part I](http://www.linksaredeleted.com/) and [Part II](http://www.linksaredeleted.com/)

* You should download both parts of homework as `.ipynb` files to the corresponding section of LMS system before the deadline.
    * When uploading multiple solutions, the last one before the deadline will be considered final (but the previous ones can help with the appeal). 
    * There are penalties for submitting your work after the deadline. They depend on how many hours late your submission are.
* **Any type of cheating will be penalized**. For example:
    * Non-compilable code won't be considered for the assessment.
    * Any type of copy-pasting part or all of the notebook will cause 0 both to subject and object of copy-pasting.
    * We are not against helping each other: we are against blind reprinting.

Don’t hesitate to contact me or teaching assistants if you have any questions! 🙂


### Part I

**Deadline: October 23, 11:59 pm**

In this part, you play the role of the Election Сommittee’s analyst. You need to prepare collected bulletins for consequent counting: check ballots for spoilage, select candidates who passed the minimum threshold, and compile a report on preliminary analysis.

There are 7 parties in our country - here's General List of Parties:
1. Harmony Party
2. Red Party 
3. Justice and Truth
4. Adventure Alliance
5. Animal Friends Party
6. Go Greens!
7. Yo-ho-ho Pirate Party

And there are two types of bulletins:
1. ones arranged in descending order of candidate priority, e.g.:  
`['Go Greens!', 'Animal Friends Party', 'Adventure Alliance', 'Yo-ho-ho Pirate Party', 'Justice and Truth', 'Harmony Party', 'Red Party']` - Go Greens! are the first choice here. Some ballot of this type may has different number of parties in it - it means that the voter simply did not choose this party (did not vote for it).  
2. with ranked positions according to General List of Parties, e.g.:
`[7, 5, 2, 1, 4, 6, 3]` - Here the Adventure Alliance has the first priority for electioneer as it's position (index `[3]`) marked with 1st place. These type of ballots could contain zeroes (meaning the voter is not interested in choosing this party); hence, there should be 7 values in the ballot.

In [284]:
general_list_of_parties = ['Harmony Party', 'Red Party', 'Justice and Truth', 'Adventure Alliance', 'Animal Friends Party', 'Go Greens!', 'Yo-ho-ho Pirate Party']

In [285]:
from csv import reader   

# read csv and delete empty rows
with open('data/votes.csv') as csv_file:
    csv_reader = reader(csv_file)
    votes = [x for x in csv_reader if x != []]

# def int_or_id(num):
#     """Convert to int if possible, otherwise keep the original."""
#     try:
#         return int(num)
#     except:
#         return num

# # convert numbers to int
# votes = map(int_or_id, votes)

print(len(votes))

13159


#### Tasks 1.1-1.2

All votes are stored together into one object. Separate this object to two containers according to bulletin type: save all bulletins with names in it to `votes_names`, others - to `votes_ranks`. After aggregating, display the sentence with lengths of each sublist using **string formatting**.

*example output:* `There are 1234 ballots with names and 1111 ballots with rankings.`

In [286]:
# 1.1-1.2 answers
# create two new empty lists
votes_names = []
votes_ranks = []

# Sort out the ballots in `votes` to new lists, one by one
for vote in votes:
    try:
        # try converting to int
        vote = map(int, vote)
        votes_ranks.append(vote)
    except ValueError:
        # int conversion failed, must be a named vote
        votes_names.append(vote)


# Display the message
print(f"There are {len(votes_names)} ballots with names and {len(votes_ranks)} ballots with rankings.")

There are 5973 ballots with names and 7186 ballots with rankings.


#### Task 1.3-1.4

Now we need to check our new lists for correctness. Let's begin with `votes_ranks`: display the **minimum**, **maximum** and **average** (rounded to three decimal places) length of ballot in this list.

*example output:*  
`Minimum ballot length: 3, `  
`Average ballot length: 4.205,`  
`Maximum ballot length: 5.`

In [287]:
# 1.3-1.4 answers

list_of_len = [len(v) for v in votes_ranks]
print(
    f"Minimum ballot length: {min(list_of_len)},\n"
    f"Average ballot length: {sum(list_of_len)/len(list_of_len):.3f},\n"
    f"Maximum ballot length: {max(list_of_len)}."
)

Minimum ballot length: 7, 
Average ballot length: 7.004, 
Maximum ballot length: 8.


Discuss: what this statistic says about this type of ballot?

***Answer:** write your answer here* 

#### Task 1.5-1.7

We know that some ballots in `votes_ranks` can contain zeros, which means voter did not include this particular party to her vote. This leads us to the following conclusions about the requirements for a valid bulletin:

1. All ballots have the same length equal to the number of parties;
1. As we have 7 parties in the race, the maximum place is 7th;
2. There should be at least 1 vote in each ballot (meaning no ballots like `[0, 0, 0, 0, 0, 0, 0]`).  

Check all three requirements in following code cells: **delete the ballot from the list if it failed to meet one of requirements**. Additionally you need to **count how many ballots were removed** after the check and display this number with some message like *"Number of incorrect ballots"* . 

In [288]:
# 1.5-1.7 answer 
incorrect_ranks = 0

votes_ranks_cleared = []

# Check that the requirements are met
for i in votes_ranks:
    if len(i) != 7 or max(i) > 7 or sum(i) < 1:
        incorrect_ranks += 1
    else:
        votes_ranks_cleared.append(i)

# Display the message below
print("Number of incorrect ballots:", incorrect_ranks)

# duplicate ranks not checked? consecutive ranks?

Number of incorrect ballots: 101


#### Tasks 1.8-1.11

 Now let's return to our `votes_names` list. There are some requirements too:

1. The number of items on the ballot should not exceed the number of parties in the general list of parties;
2. At least one party should be chosen by each voter.

Check all three requirements in following code cells: **delete the ballot from the list if it failed to meet one of requirements**. Additionally you need to **count how many ballots were removed** after the check and display this number with some message like *"Number of incorrect ballots"* (task 1.6). 


In [289]:
# 1.8-1.11 answer 
incorrect = 0

# Check that the requirements 1-2 are met (length of ballot)
votes_names_cleared = []

for i in votes_names:
    if 1 <= len(i) <= 7:
        votes_names_cleared.append(i)
    else:
        incorrect += 1

# Display the message below
print("Number of incorrect ballots:", incorrect)

Number of incorrect bulletins: 58


**\*Advanced task**. Complete tasks 1.8-1.11 with [list comprehensions](https://www.w3schools.com/python/python_lists_comprehension.asp)

In [290]:
votes_names_cleared = [
    vote 
    for vote in votes_names 
    if 1 <= len(vote) <= 7
]
# votes_names_cleared = [vote for vote in votes_names for party in vote if party in general_list_of_parties]

print("Number of incorrect ballots:", len(votes_names) - len(votes_names_cleared))

Number of incorrect bulletins: 58


#### Task 1.12-1.13

It is uncomfortable to store data in two different formats. Let's:  
1. convert `votes_ranks` to `votes_names` format;  
2. bind this new list with already existing names ballots;
3. display the message of total number of valid ballots.

*example output:*  
`Total number of valid ballots: 2500`  

How to convert: use `general_list_of_parties` to recall the order of parties in the ballot, e.g.:  
`[0,0,1,0,3,0,2]` -> `['Justice and Truth', 'Yo-ho-ho Pirate Party', 'Animal Friends Party']` 

*Hint: to use this, you need to combine [this piece of code](https://stackoverflow.com/a/6618543/10803427) with some condition for zeros*

In [291]:
len(votes_ranks_cleared) + len(votes_names_cleared)

13000

In [292]:
# 1.12-1.13 answer 

# create a new list
newlist = []

# fill the gaps in the code
for vote in votes_ranks_cleared:
    newlist.append([
        name 
        for rank, name in sorted(zip(vote, general_list_of_parties)) 
        if rank != 0
    ])

# bind two lists together

votes_names_cleared.extend(newlist)

# display the message
print(f"Total number of valid ballots: {len(votes_names_cleared)}") 

Total number of valid ballots: 13000


#### Tasks 1.14-1.15

Now we need to check all parties for passing the required threshold. As all ballots in our country are ranked one, we can expect many parties to be named in different ballots (the sum of probabilities wont be equal to 1, as it is in one-choice elections), so let's set a 40% passing threshold. 
1. Create the list of `passed_parties`;  
2. Calculate the share of votes for each party separately. If the party has not crossed the threshold, it won't be represented in succeed list;  
3. Display a list of succeed parties along with the corresponding message.

example output: `['Justice and Truth', 'Animal Friends Party', 'Go Greens!', 'Yo-ho-ho Pirate Party'] passed the 40% threshold!`

In [293]:
# 1.14-1.15 answer   # 40% doesn't match the initial text

# ranked voting doesn't usually have thresholds, since it's a majority-based system

# create a dictionary where you will count occurrences
number_of_votes = {}
for party in general_list_of_parties: 
    number_of_votes[party] = 0

# number_of_votes = { party:0 for party in general_list_of_parties }

# create a list of passed parties
passed_parties = []

# calculate total votes for each party
for vote in votes_names:
    for party in vote:
        number_of_votes[party] += 1 # vote.count(party) # DOUBLE COUNTING!

# calculate the share of each party: if passed, append to the list of passed_parties
for party, votes in number_of_votes.items():
    fraction = votes / len(votes_names)
    if fraction >= 0.4:
        passed_parties.append(party)

# display the message
print(passed_parties, "passed the 40% threshold!")

['Harmony Party', 'Red Party', 'Justice and Truth', 'Adventure Alliance', 'Animal Friends Party'] passed the 40% threshold!


**\*Advanced task**. Complete tasks 1.14-1.15 with dict and list comprehensions.

#### Task 1.16

Preparations are almost complete. It remains to eliminate the parties that did not pass from the ballots.

1. Create a list of failed parties and display it
2. Remove these parties from ballots.

*example output:*  
`['Harmony Party', 'Red Party', 'Adventure Alliance'] failed to pass the 5% threshold`

In [294]:
#  task 1.16

# create a list of failed parties
failed_parties = []

# append failed parties to the list
for party in general_list_of_parties:
    if party not in passed_parties:
        failed_parties.append(party)

# failed_parties = set(general_list_of_parties) - set(passed_parties)

# display the message 
print(failed_parties, "failed to pass the 40% threshold")

# remove them from ballots
final_votes = []

for vote in votes_names:
    new_vote = [party for party in vote if party not in failed_parties]
    final_votes.append(new_vote)

['Go Greens!', 'Yo-ho-ho Pirate Party'] failed to pass the 40% threshold


Now, when all the votes are cleared and prepared, we are ready to start the count!

This is the end of Part I of the Homework Assignment. Make sure that all code cells in your notebook are executable and without Errors, and submit your homework via [SmartLMS](https://edu.hse.ru/mod/assign/view.php?id=613078). 

### Part II

**Deadline: October 30, 11:59 pm**

For the second part of your homework, you need to calculate the winner of election with different voting techniques. All descriptions were taken from the ***Voting Methods*** paper from [Stanford Encyclopedia of Philosophy Archive](https://plato.stanford.edu/archives/fall2019/entries/voting-methods/#toc).

We will store each winner to the `final_results` dictionary to eventually compare all methods between one another.

In [295]:
# Don't forget to run this code line!
final_results = dict()

#### Single-Member Plurality Voting (first-past-the-post)

Plurality rule (also called First-Past-the-Post rule) is the simplest method of votes counting, which is widely used despite its known problems.

> Description: 
>
> Each voter selects one candidate (or none if voters can abstain), and the candidate(s) with the most votes win.

To count with first-past-the-post voting method, recall which object stores counts of favourite candidates. 
1. Count number of 1st votes all over the ballots we have. Store results in some dictionary with party name as key and number of votes as value;  
2. Rearrange the dictionary with counted votes in a descending order by number of votes;   
4. Save the winner to `final_results` dictionary;  
3. Print a short news message announcing the results of the election (use string formatting to display name and number of votes, no copypasta here):  

*example output:*  
`The results of the last election: `  
`According to the first-past-the-post voting system, Yo-ho-ho Pirate Party won with 9999 votes!`

In [296]:
# Count 1st votes
firsts = [vote[0] for vote in final_votes]

pluralism = {party: firsts.count(party) for party in passed_parties}

pluralism = sorted(pluralism.items(), key=lambda item: item[1], reverse=True)

# Display the message
print(f"The results of the last election: \nAccording to the first-past-the-post voting system, {pluralism[0][0]} won with {pluralism[0][1]} votes!")

# Save the result
final_results['pluralism'] = pluralism[0][0]

The results of the last election: 
According to the first-past-the-post voting system, Harmony Party won with 1252 votes!


In [297]:
pluralism

[('Harmony Party', 1252),
 ('Justice and Truth', 1243),
 ('Adventure Alliance', 1166),
 ('Red Party', 1163),
 ('Animal Friends Party', 1149)]

#### Borda Count

Borda Counting is the most popular instance of ranking methods. Despite they are much more expensive than selecting a single candidate, they demonstrate more fair calculations.

> Description: 
>
>Each voter provides a ranking of the candidates. Then, a score (the Borda score) is assigned to each candidate by a voter as follows: If there are n candidates, give n−1 points to the candidate ranked first, n−2 points to the candidate ranked second,…, 1 point to the candidate ranked second to last and 0 points to candidate ranked last.

To complete Borda count, you need:
1. Create new dict to store Borda scores;
2. Increase the score of party according to its position in ballot; 
3. Rearrange the dictionary with counted votes in a descending order by number of votes;   
4. Save the Borda winner to `final_results` dictionary;  
6. Print a short news message announcing the results of the election (use string formatting to display name and number of votes, no copypasta here either): 

*example output:*  
`The results of the last election: `  
`According to the Borda system, Yo-ho-ho Pirate Party won with 9999 votes!`

*Note: as here we range all the candidates from the ballot, we need to determine how many parties were included by voter. This variable could also be used as a descending counter for Borda scores.*

In [298]:
# Create a dict for borda scores
borda = {party: 0 for party in passed_parties}

# Calculate number of votes for each party according to Borda rule
for vote in final_votes:  
    k = len(passed_parties)-1
    for party in vote:
        borda[party] += k
        k -=1

# Sort this dict by value in descending order
borda = sorted(borda.items(), key=lambda item: item[1], reverse=True)

# Display the message
print(f"The results of the last election: \nAccording to the Borda system, {borda[0][0]} won with {borda[0][1]} points!")

# Save the result
final_results['borda'] = borda[0][0]

The results of the last election: 
According to the Borda system, Justice and Truth won with 9222 votes!


In [299]:
borda

[('Justice and Truth', 9222),
 ('Harmony Party', 9180),
 ('Red Party', 9016),
 ('Adventure Alliance', 8824),
 ('Animal Friends Party', 8808)]

#### Condorcet Count

The idea of Condorcet voting is to make a set of one-on-one electons. The candidate that beat all others in one-by-one wins the election.

> Description: 
>
> Given a ranking from each voter, the majority relation orders the candidates in terms of how they perform in one-on-one elections. A candidate is called the Condorcet winner in an election scenario if she has the maximum of the majority ordering for that election scenario. The Condorcet loser is the candidate that is the minimum of the majority ordering.

Let's wrap up the idea of Condorcet winner in programming logic:

1. Create new dict to store all pairwise comparisons;
2. Calculate the share of ballots in which one candidate beats antoher, and store the share of such cases to corresponding slot.
3. Save the Condorcet winner to `final_results` dictionary;  
4. Print a short news message announcing the results of the election (use string formatting to display name of party, no copypasta here either): 

*example output:*  
`The results of the last election: `  
`According to the Condorcet system, Yo-ho-ho Pirate Party won!`

*Note:*

In [300]:
# Create an empty list of parvise combinations
combinations = []

# Store all possible pairs in this list as set of 2 party names
for party1 in passed_parties:
     for party2 in passed_parties:
        combination = {party1, party2}
        # skip the iteration if there's only one party in set or the combination already exists
        if (len(combination) == 1) or (combination in combinations):
            continue
        # append combination to the list of combinations
        combinations.append(combination)

combinations

# use itertools!
# combinations = itertools.combinations(passed_parties, 2)

[{'Harmony Party', 'Red Party'},
 {'Harmony Party', 'Justice and Truth'},
 {'Adventure Alliance', 'Harmony Party'},
 {'Animal Friends Party', 'Harmony Party'},
 {'Justice and Truth', 'Red Party'},
 {'Adventure Alliance', 'Red Party'},
 {'Animal Friends Party', 'Red Party'},
 {'Adventure Alliance', 'Justice and Truth'},
 {'Animal Friends Party', 'Justice and Truth'},
 {'Adventure Alliance', 'Animal Friends Party'}]

In [301]:
final_votes[0]

['Adventure Alliance',
 'Harmony Party',
 'Justice and Truth',
 'Animal Friends Party',
 'Red Party']

In [302]:
non_losers = set(passed_parties)

for combination in combinations:
    party_0, party_1 = combination 

    # create a counter with 0 value
    counter = 0

    # NEGATIONS UPON NEGATIONS MAKE TRACING HARD
    # calculate which party has the biggest priority for each ballot
    for vote in final_votes:
        if party_0 in vote:
            candidate_0_score = vote[::-1].index(party_0)
        else:
            candidate_0_score = 0
        if party_1 in vote:
            candidate_1_score = vote[::-1].index(party_1)
        else:
            candidate_1_score = 0

        # move counter correspondingly
        if candidate_0_score > candidate_1_score:
            counter += 1
        elif candidate_1_score > candidate_0_score:
            counter -= 1
        else:
            continue

    # display the pairwise winner with correct counter conditions
    if counter > 0:
        print(f"{party_0} beats {party_1}")
        if party_1 in non_losers:
            non_losers.remove(party_1) 
    elif counter < 0:
        print(f"{party_1} beats {party_0}")
        if party_0 in non_losers:
            non_losers.remove(party_0) 
    else:
        print(f"There is no winner between {party_0} and {party_1}")

final_results['condorcet'] = list(non_losers)[0]

Harmony Party beats Red Party
Justice and Truth beats Harmony Party
Harmony Party beats Adventure Alliance
Harmony Party beats Animal Friends Party
Justice and Truth beats Red Party
Red Party beats Adventure Alliance
Red Party beats Animal Friends Party
Justice and Truth beats Adventure Alliance
Justice and Truth beats Animal Friends Party
Adventure Alliance beats Animal Friends Party


#### Summary

**\*Advanced task:** to wrap-up the assignment, display the `final_results` dictionary of the winners by different methods. Which method seemed the fairest to you? What are the advantages and disadvantages of each method? Using the scientific literature, write a short, detailed answer (200 words minimum). Don't forget to cite references.

In [303]:
final_results

{'pluralism': 'Harmony Party',
 'borda': 'Justice and Truth',
 'condorcet': 'Justice and Truth'}

***Answer:** write your answer here* 

This is the end of Part II of the Homework Assignment. Make sure that all code cells in your notebook are executable and without Errors, and submit your homework via [LMS](http://www.linksaredeleted.com/). 